In [1]:
using Revise
using ShadyPolytopes
using Polyhedra
using Printf
using LaTeXStrings
using SCS
using Latexify

In [2]:
using WGLMakie, Bonito
Page(offline=true) 
WGLMakie.activate!()

# Inscribed and circumscribed sphere of $\mathcal{C}$

In [3]:
function euclidean_norm(x)
    return sqrt(sum(t^2 for t in x))
end

function plot_inner_and_outer_sphere(cscb; color=:cornflowerblue)
    vertices = all_vertices(cscb)
    r = minimum(1/euclidean_norm(w) for w in cscb.normals)
    R = maximum(euclidean_norm(v) for v in vertices)
    display(@sprintf "R = %.3f" R)
    display(@sprintf "r = %.3f" r)
    display(@sprintf "R/r = %.3f" R/r)
    display("spectral norm bound squared: $(determine_squared_spectralnorm_bound(cscb))")
    display(@sprintf "spectral norm bound = %.3f" sqrt(determine_squared_spectralnorm_bound(cscb)))
    p = polyhedron(convexhull(convert(Vector{Vector{Float64}},vertices)...))
    n = Polyhedra.Mesh(p)
    fig,ax,P = mesh(n, transparency=true, alpha=0.7, color=color); 
    wireframe!(ax, n, color=:black, transparency=true, alpha=0.3, linewidth=1);
    outer_sphere = mesh!(ax,Sphere(Point3f(0),R), transparency=true, alpha=0.2, color=:grey)
    inner_sphere = mesh!(ax,Sphere(Point3f(0),r), transparency=true, alpha=0.3, color=:black)
    return fig
end
display(L"Analyzing $\mathcal{I}$")
display(ShadyPolytopes.perturbed_icosahedron(-3//5,-1//5,1//10))

fig = plot_inner_and_outer_sphere(optimal_icosahedron);

L"Analyzing $\mathcal{I}$"

CSCP{Rational{BigInt}}(Vector{Rational{BigInt}}[[1, -3//5, 1//10], [1, -1//5, 1//10], [1//10, 1, -3//5], [1//10, 1, -1//5], [-3//5, 1//10, 1], [-1//5, 1//10, 1]], Vector{Rational{BigInt}}[[390//1069, -1250//1069, -710//1069], [710//1069, -390//1069, 1250//1069], [20//53, -55//53, 0], [-710//1069, 390//1069, -1250//1069], [-15//17, 0, -20//17], [-10//9, -10//9, -10//9], [-55//53, 0, 20//53], [-1250//1069, -710//1069, 390//1069], [0, -20//53, 55//53], [-20//17, -15//17, 0], [0, 20//17, 15//17], [-390//1069, 1250//1069, 710//1069], [-20//53, 55//53, 0], [0, -20//17, -15//17], [0, 20//53, -55//53], [1250//1069, 710//1069, -390//1069], [10//9, 10//9, 10//9], [20//17, 15//17, 0], [15//17, 0, 20//17], [55//53, 0, -20//53]])

"R = 1.170"

"r = 0.520"

"R/r = 2.253"

"spectral norm bound squared: 137//27"

"spectral norm bound = 2.253"

In [4]:
fig

# Transformation into approximate John position

In [5]:
M = approximate_john_position(optimal_icosahedron)
display(latexify(M))

-------------------------------------------------------------
           Clarabel.jl v0.10.0  -  Clever Acronym              
                   (c) Paul Goulart                          
                University of Oxford, 2022                   
-------------------------------------------------------------

chordal decomposition:
compact format = on, dual completion = oncronym              
                   (c) Paul Goulart                          
                University of Oxford, 2022                   
-------------------------------------------------------------

chordal decomposition:

  merge method = clique_graph
  PSD cones initial             = 3
  PSD cones decomposable        = 1
  PSD cones after decomposition = 5
  PSD cones after merges        = 5

problem:
  variables     = 22
  constraints   = 62
  nnz(P)        = 0
  nnz(A)        = 238
  cones (total) = 9
    : Nonnegative = 2,  numel = (1,20)
    : Power       = 2,  numel = (3,3)
    : PSDTriangle = 5,  nu

L"\begin{equation}
\left[
\begin{array}{ccc}
\frac{11}{10} & \frac{11}{10} & \frac{11}{10} \\
0 & \frac{-4}{5} & \frac{4}{5} \\
1 & \frac{-1}{2} & \frac{-2}{5} \\
\end{array}
\right]
\end{equation}
"

In [6]:
display(L"Analyzing $\mathcal{J} = M \mathcal{I}$")
display([M*x for x in optimal_icosahedron.positive_vertices])
display(optimal_icosahedron_john_position.positive_vertices)

fig = plot_inner_and_outer_sphere(optimal_icosahedron_john_position; color=:yellowgreen)
display(fig)
display("1.55 > spectral_norm_bound: ")
display((155//100)^2 > determine_squared_spectralnorm_bound(optimal_icosahedron_john_position))

L"Analyzing $\mathcal{J} = M \mathcal{I}$"

6-element Vector{Vector{Rational{BigInt}}}:
 [11//20, 14//25, 63//50]
 [99//100, 6//25, 53//50]
 [11//20, -32//25, -4//25]
 [99//100, -24//25, -8//25]
 [11//20, 18//25, -21//20]
 [99//100, 18//25, -13//20]

6-element Vector{Vector{Rational{BigInt}}}:
 [11//20, 49//100, 117//100]
 [99//100, 57//100, 81//100]
 [11//20, 81//100, -51//50]
 [99//100, 9//20, -9//10]
 [11//20, -13//10, -3//20]
 [99//100, -51//50, 9//100]

"R = 1.424"

"r = 0.923"

"R/r = 1.543"

"spectral norm bound squared: 370280747942//155558341125"

"spectral norm bound = 1.543"

"1.55 > spectral_norm_bound: "

true

# Determining a projection with small norm

In [17]:
function makie_polyhedron(vertices)
    vertices = convert(Vector{Vector{Float64}},vertices)
    p = polyhedron(convexhull(vertices...))
    return Polyhedra.Mesh(p)
end

function plot_projection(cscb; color=:cornflowerblue)
    vertices = all_vertices(cscb)
    n = makie_polyhedron(vertices)
    fig,ax,P = mesh(n, transparency=true, alpha=0.7, color=color); 
    wireframe!(ax, n, color=:black, transparency=true, alpha=0.3, linewidth=1);
    proj, shadiness_const = ShadyPolytopes.find_shadiness_constant_numerically(cscb, false)
    approx_proj = ShadyPolytopes.approximate_projection(proj,prec=10^4)
    image = makie_polyhedron([1.2*approx_proj*v for v in vertices])
    mesh!(ax, image, transparency=true, alpha=0.9, color=:darkred);
    kernel = proj*[1,1,0]-[1,1,0]
    lines!(ax, [Point3f(kernel),Point3f(-kernel)],  transparency=true, alpha=0.5,color=:darkred);
    display(@sprintf "s_2 ≈ %.6f" shadiness_const)
    display(@sprintf "s_2 ≤ %.6f" ShadyPolytopes.operator_norm(cscb, approx_proj))
    display("Projection: ")
    display(latexify(approx_proj))
    op_norm = ShadyPolytopes.operator_norm(cscb, approx_proj)
    display("Operator norm of projection = $op_norm ≈ "*(@sprintf "%.5f" op_norm))
    return fig, approx_proj
end

fig, approx_proj = plot_projection(optimal_icosahedron)
fig

presolving:
(round 1, fast)       0 del vars, 1 del conss, 0 add conss, 1 chg bounds, 0 chg sides, 0 chg coeffs, 1 upgd conss, 0 impls, 0 clqs
   (0.0s) symmetry computation started: requiring (bin +, int +, cont +), (fixed: bin -, int -, cont -)
   (0.0s) symmetry computation finished: 1 generators found (max: 1500, log10 of symmetry group size: 0.0) (symcode time: 0.00)
dynamic symmetry handling statistics:
   orbitopal reduction:       no components
   orbital reduction:         no components
   lexicographic reduction:   no permutations
handled 1 out of 1 symmetry components
(round 2, exhaustive) 0 del vars, 1 del conss, 2 add conss, 1 chg bounds, 0 chg sides, 0 chg coeffs, 1 upgd conss, 0 impls, 0 clqs
presolving (3 rounds: 3 fast, 2 medium, 2 exhaustive):
 0 deleted vars, 1 deleted constraints, 0 added constraints, 1 tightened bounds, 0 added holes, 0 changed sides, 0 changed coefficients
 0 implications, 0 cliques
presolved problem has 10 variables (0 bin, 0 int, 0 impl, 10 cont

"s_2 ≈ 1.012713"

"s_2 ≤ 1.012747"

"Projection: "

L"\begin{equation}
\left[
\begin{array}{ccc}
\frac{82602121}{79729122} & \frac{54836807}{79729122} & \frac{-722323}{13288187} \\
\frac{-4217717}{79729122} & \frac{-774259}{79729122} & \frac{1060409}{13288187} \\
\frac{695635}{39864561} & \frac{13277555}{39864561} & \frac{12938397}{13288187} \\
\end{array}
\right]
\end{equation}
"

"Operator norm of projection = 14386149522//14205071903 ≈ 1.01275"